In [ ]:
from IPython.display import Image, SVG, display
from tqdm import tqdm
import matplotlib.pyplot as plt
import sys
import subprocess
import pkg_resources
import numpy as np
import pandas as pd
import os
from skimage.io import imread
import cv2 as cv
from pathlib import Path
import random
from shutil import copyfile, rmtree
import json
import seaborn as sns
import matplotlib
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
import tensorflow as tf
from tensorflow import keras
import os
import time

In [ ]:
from training.data_load import load_data

train_ds, test_ds, validation_ds = load_data((227, 227), './new_data_transformed/train', './new_data_transformed/test')

In [ ]:
def tensorboard_callback(model_name):
    return keras.callbacks.TensorBoard(os.path.join(f"./logs/{model_name}", time.strftime("run_%Y_%m_%d-%H_%M_%S")))

In [ ]:
model = keras.models.Sequential([
    keras.layers.Conv2D(filters=96, kernel_size=(11,11), strides=(4,4), activation='relu', input_shape=(227,227,3)),
    keras.layers.BatchNormalization(),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Conv2D(filters=256, kernel_size=(5,5), strides=(1,1), activation='relu', padding="same"),
    keras.layers.BatchNormalization(),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Conv2D(filters=384, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.BatchNormalization(),
    keras.layers.Conv2D(filters=384, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.BatchNormalization(),
    keras.layers.Conv2D(filters=256, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.BatchNormalization(),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Flatten(),
    keras.layers.Dense(4096, activation='relu'),
    keras.layers.Dense(4096, activation='relu'),
    keras.layers.Dense(6, activation='softmax')
])

In [ ]:
model.compile(loss='sparse_categorical_crossentropy', optimizer=tf.optimizers.SGD(learning_rate=.001), metrics=['accuracy'])
model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d (Conv2D)             (None, 55, 55, 96)        34944     
                                                                 
 batch_normalization (BatchN  (None, 55, 55, 96)       384       
 ormalization)                                                   
                                                                 
 max_pooling2d (MaxPooling2D  (None, 27, 27, 96)       0         
 )                                                               
                                                                 
 conv2d_1 (Conv2D)           (None, 27, 27, 256)       614656    
                                                                 
 batch_normalization_1 (Batc  (None, 27, 27, 256)      1024      
 hNormalization)                                                 
                                                        

In [ ]:
model.fit(train_ds,
          epochs=50,
          validation_data=validation_ds,
          validation_freq=1,
          callbacks=[tensorboard_callback("AlexNet")])

Epoch 1/50
45/45 [==============================] - 13s 82ms/step - loss: 1.5723 - accuracy: 0.4535 - val_loss: 1.8094 - val_accuracy: 0.1676
Epoch 2/50
45/45 [==============================] - 3s 60ms/step - loss: 0.8888 - accuracy: 0.6771 - val_loss: 1.8356 - val_accuracy: 0.1733
Epoch 3/50
45/45 [==============================] - 3s 62ms/step - loss: 0.7100 - accuracy: 0.7292 - val_loss: 1.8753 - val_accuracy: 0.1534
Epoch 4/50
45/45 [==============================] - 3s 61ms/step - loss: 0.5200 - accuracy: 0.8222 - val_loss: 1.9177 - val_accuracy: 0.1477
Epoch 5/50
45/45 [==============================] - 3s 60ms/step - loss: 0.3887 - accuracy: 0.8868 - val_loss: 2.0252 - val_accuracy: 0.1591
Epoch 6/50
45/45 [==============================] - 3s 60ms/step - loss: 0.2841 - accuracy: 0.9340 - val_loss: 2.0583 - val_accuracy: 0.2273
Epoch 7/50
45/45 [==============================] - 3s 60ms/step - loss: 0.2114 - accuracy: 0.9569 - val_loss: 2.1366 - val_accuracy: 0.2216
Epoch 8/50
4

In [ ]:
!tensorboard dev upload --logdir logs/AlexNet --name AlexNetFish


***** TensorBoard Uploader *****

This will upload your TensorBoard logs to https://tensorboard.dev/ from
the following directory:

logs/AlexNet

This TensorBoard will be visible to everyone. Do not upload sensitive
data.

Your use of this service is subject to Google's Terms of Service
<https://policies.google.com/terms> and Privacy Policy
<https://policies.google.com/privacy>, and TensorBoard.dev's Terms of Service
<https://tensorboard.dev/policy/terms/>.

This notice will not be shown again while you are logged into the uploader.
To log out, run `tensorboard dev auth revoke`.

Continue? (yes/NO) yes

Please visit this URL to authorize this application: https://accounts.google.com/o/oauth2/auth?response_type=code&client_id=373649185512-8v619h5kft38l4456nm2dj4ubeqsrvh6.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=openid+https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fuserinfo.email&state=4s45OaCdh7CXhhMYUBHIgm6u6oiMTE&prompt=consent&access_type=offline


In [ ]:
model.evaluate(test_ds)


9/9 [==============================] - 0s 32ms/step - loss: 0.9122 - accuracy: 0.7188


[0.9122310280799866, 0.71875]

In [ ]:
from training.model_freeze import freeze_model

freeze_model(model, './frozen_models', "frozen_alex_net")